# Machine Translation using OpenNMT

# Jamo and Char Tokenization

In [1]:
cd /home/ubuntu/MT

/home/ubuntu/MT


In [3]:
!pip install hgtk

Looking in indexes: http://ftp.daumkakao.com/pypi/simple
  Created wheel for hgtk: filename=hgtk-0.1.3-py2.py3-none-any.whl size=6689 sha256=c79e1449aa15b61035cead5f6ce27dcce6f4dc168f720c8444872605bbc5f22e
  Stored in directory: /home/ubuntu/.cache/pip/wheels/96/10/4b/0887dcaf5e0b0d26b807fef3497703fea2c44a76f91d198bd3
Successfully built hgtk


In [50]:
!python OpenNMT-py/tools/apply_jamo.py -i OpenNMT-py/Data/src-train.txt -o OpenNMT-py/Data/src-train-jamo.txt
!python OpenNMT-py/tools/apply_jamo.py -i OpenNMT-py/Data/src-valid.txt -o OpenNMT-py/Data/src-val-jamo.txt
!python OpenNMT-py/tools/apply_jamo.py -i OpenNMT-py/Data/src-test.txt -o OpenNMT-py/Data/src-test-jamo.txt
!python OpenNMT-py/tools/apply_char.py -i OpenNMT-py/Data/tgt-train.txt -o OpenNMT-py/Data/tgt-train-char.txt
!python OpenNMT-py/tools/apply_char.py -i OpenNMT-py/Data/tgt-valid.txt -o OpenNMT-py/Data/tgt-val-char.txt
!python OpenNMT-py/tools/apply_char.py -i OpenNMT-py/Data/tgt-test.txt -o OpenNMT-py/Data/tgt-test-char.txt

# **Preprocess the data**

We will be working with some example data in data/ folder.

The data consists of parallel source (src) and target (tgt) data containing one sentence per line with tokens separated by a space:

1. src-train.txt

2. tgt-train.txt

3. src-val.txt

4. tgt-val.txt


Train data and validataion data are required for machine translation training.

Validation files are required and used to evaluate the convergence of the training. It usually contains no more than 5000 sentences.


> If you think about it briefly, you can specify the path of train data and validation data, and specify the path and name to save in -save_data.

> If you want to set vocab size add below command
<br>
-src_vocab_size 32000 -tgt_vocab_size 32000

The vocab size is usually 32000.

In [51]:
!python OpenNMT-py/preprocess.py -train_src OpenNMT-py/Data/src-train-jamo.txt -train_tgt OpenNMT-py/Data/tgt-train-char.txt -valid_src OpenNMT-py/Data/src-val-jamo.txt -valid_tgt OpenNMT-py/Data/tgt-val-char.txt -save_data OpenNMT-py/Data/jamo2char/demo -src_vocab_size -1 -tgt_vocab_size -1 -overwrite

[2020-12-06 23:32:05,729 INFO] Extracting features...
[2020-12-06 23:32:05,729 INFO]  * number of source features: 0.
[2020-12-06 23:32:05,729 INFO]  * number of target features: 0.
[2020-12-06 23:32:05,729 INFO] Building `Fields` object...
[2020-12-06 23:32:05,729 INFO] Building & saving training data...
[2020-12-06 23:32:05,730 WARNING] Shards for corpus train already exist, will be overwritten because `-overwrite` option is set.
[2020-12-06 23:32:05,739 WARNING] Overwrite shards for corpus None
[2020-12-06 23:32:18,099 INFO] Building shard 0.
[2020-12-06 23:33:57,845 INFO]  * saving 0th train data shard to OpenNMT-py/Data/jamo2char/demo.train.0.pt.
[2020-12-06 23:33:58,652 INFO]  * tgt vocab size: 50.
[2020-12-06 23:33:58,653 INFO]  * src vocab size: 81.
[2020-12-06 23:33:58,658 INFO] Building & saving validation data...
[2020-12-06 23:33:58,658 WARNING] Shards for corpus valid already exist, will be overwritten because `-overwrite` option is set.
[2020-12-06 23:33:58,688 WARNING] O

!python OpenNMT-py/preprocess.py -train_src OpenNMT-py/Data/src-train-bpe.txt -train_tgt OpenNMT-py/Data/tgt-train-bpe.txt -valid_src OpenNMT-py/Data/src-val-bpe.txt -valid_tgt OpenNMT-py/Data/tgt-val-bpe.txt -save_data OpenNMT-py/Data/demo -src_vocab_size 32000 -tgt_vocab_size 32000

# **Train the data(Transformer)**

https://papers.nips.cc/paper/7181-attention-is-all-you-need.pdf


> If you get GPU-related errors, try halving batch_size

**Below is the full command, and if you want to know more about it, search about Transformer.**

!python OpenNMT-py/train.py -data OpenNMT-py/data/demo -save_model OpenNMT-py/data/model/model -layers 6 -rnn_size 512 -word_vec_size 512 -transformer_ff 2048 -heads 8 -encoder_type transformer -decoder_type transformer -position_encoding -train_steps 200000 -max_generator_batches 2 -dropout 0.1 -batch_size 4096 -batch_type tokens -normalization tokens -accum_count 2 -optim adam -adam_beta2 0.998 -decay_method noam -warmup_steps 8000 -learning_rate 2 -max_grad_norm 0 -param_init 0 -param_init_glorot -label_smoothing 0.1 -valid_steps 1000 -save_checkpoint_steps 1000 -world_size 1 -gpu_rank 0  

In [52]:
!nvidia-smi

Sun Dec  6 23:34:06 2020       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 440.64       Driver Version: 440.64       CUDA Version: 10.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|===============================+======================+======================|
|   0  Quadro RTX 6000     On   | 00000000:00:06.0 Off |                    0 |
| N/A   25C    P8    12W / 250W |      0MiB / 22698MiB |      0%      Default |
+-------------------------------+----------------------+----------------------+
                                                                               
+-----------------------------------------------------------------------------+
| Processes:                                                       GPU Memory |
|  GPU  

In [53]:
!python OpenNMT-py/train.py -data OpenNMT-py/Data/jamo2char/demo -save_model OpenNMT-py/Data/jamo2char/model/model -layers 6 -rnn_size 512 -word_vec_size 512 -transformer_ff 2048 -heads 8 -encoder_type transformer -decoder_type transformer -position_encoding -train_steps 50000 -max_generator_batches 2 -dropout 0.1 -batch_size 4096 -batch_type tokens -normalization tokens -accum_count 2 -optim adam -adam_beta2 0.998 -decay_method noam -warmup_steps 8000 -learning_rate 2 -max_grad_norm 0 -param_init 0 -param_init_glorot -label_smoothing 0.1 -valid_steps 1000 -save_checkpoint_steps 100 -world_size 1 -gpu_rank 0 -tensorboard -tensorboard_log_dir 'logs/my_board/jamo2char'

[2020-12-06 23:34:18,186 INFO]  * src vocab size = 81
[2020-12-06 23:34:18,186 INFO]  * tgt vocab size = 50
[2020-12-06 23:34:18,186 INFO] Building model...
[2020-12-06 23:34:24,203 INFO] NMTModel(
  (encoder): TransformerEncoder(
    (embeddings): Embeddings(
      (make_embedding): Sequential(
        (emb_luts): Elementwise(
          (0): Embedding(81, 512, padding_idx=1)
        )
        (pe): PositionalEncoding(
          (dropout): Dropout(p=0.1, inplace=False)
        )
      )
    )
    (transformer): ModuleList(
      (0): TransformerEncoderLayer(
        (self_attn): MultiHeadedAttention(
          (linear_keys): Linear(in_features=512, out_features=512, bias=True)
          (linear_values): Linear(in_features=512, out_features=512, bias=True)
          (linear_query): Linear(in_features=512, out_features=512, bias=True)
          (softmax): Softmax(dim=-1)
          (dropout): Dropout(p=0.1, inplace=False)
          (final_linear): Linear(in_features=512, out_features=512,

[2020-12-06 23:34:24,287 INFO] Starting training on GPU: [0]
[2020-12-06 23:34:24,287 INFO] Start training loop and validate every 1000 steps...
[2020-12-06 23:34:24,288 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-06 23:34:24,364 INFO] number of examples: 1803
[2020-12-06 23:34:28,728 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-06 23:34:28,852 INFO] number of examples: 1803
[2020-12-06 23:34:33,367 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-06 23:34:33,440 INFO] number of examples: 1803
[2020-12-06 23:34:37,475 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-06 23:34:37,551 INFO] number of examples: 1803
[2020-12-06 23:34:42,013 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-06 23:34:42,085 INFO] number of examples: 1803
[2020-12-06 23:34:43,542 INFO] Step 50/50000; acc:   9.41; ppl: 25.36; xent: 3.23; lr: 0.00001; 18873/176

[2020-12-06 23:37:40,277 INFO] number of examples: 1803
[2020-12-06 23:37:42,513 INFO] Step 500/50000; acc:  37.21; ppl:  5.73; xent: 1.75; lr: 0.00006; 18962/17672 tok/s;    198 sec
[2020-12-06 23:37:42,518 INFO] Saving checkpoint OpenNMT-py/Data/jamo2char/model/model_step_500.pt
[2020-12-06 23:37:46,211 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-06 23:37:46,281 INFO] number of examples: 1803
[2020-12-06 23:37:50,482 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-06 23:37:50,600 INFO] number of examples: 1803
[2020-12-06 23:37:55,107 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-06 23:37:55,179 INFO] number of examples: 1803
[2020-12-06 23:37:59,335 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-06 23:37:59,409 INFO] number of examples: 1803
[2020-12-06 23:38:03,173 INFO] Step 550/50000; acc:  39.21; ppl:  5.42; xent: 1.69; lr: 0.00007; 17727/16448 tok/s;   

[2020-12-06 23:40:59,513 INFO] number of examples: 1803
[2020-12-06 23:41:03,653 INFO] Step 1000/50000; acc:  58.79; ppl:  3.11; xent: 1.13; lr: 0.00012; 19081/17702 tok/s;    399 sec
[2020-12-06 23:41:03,655 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.valid.0.pt
[2020-12-06 23:41:04,805 INFO] number of examples: 8014
[2020-12-06 23:41:40,684 INFO] Validation perplexity: 22.6989
[2020-12-06 23:41:40,685 INFO] Validation accuracy: 18.6862
[2020-12-06 23:41:40,691 INFO] Saving checkpoint OpenNMT-py/Data/jamo2char/model/model_step_1000.pt
[2020-12-06 23:41:43,221 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-06 23:41:43,307 INFO] number of examples: 1803
[2020-12-06 23:41:47,916 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-06 23:41:47,989 INFO] number of examples: 1803
[2020-12-06 23:41:52,204 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-06 23:41:52,277 INFO] number of examples:

[2020-12-06 23:44:50,074 INFO] number of examples: 1803
[2020-12-06 23:44:54,586 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-06 23:44:54,664 INFO] number of examples: 1803
[2020-12-06 23:44:58,922 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-06 23:44:59,105 INFO] number of examples: 1803
[2020-12-06 23:45:03,736 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-06 23:45:03,812 INFO] number of examples: 1803
[2020-12-06 23:45:05,693 INFO] Step 1500/50000; acc:  85.89; ppl:  1.59; xent: 0.46; lr: 0.00019; 18621/17353 tok/s;    641 sec
[2020-12-06 23:45:05,697 INFO] Saving checkpoint OpenNMT-py/Data/jamo2char/model/model_step_1500.pt
[2020-12-06 23:45:10,443 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-06 23:45:10,515 INFO] number of examples: 1803
[2020-12-06 23:45:15,027 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-06 23:45:15,1

...

[2020-12-07 05:30:33,097 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-07 05:30:33,175 INFO] number of examples: 1803
[2020-12-07 05:30:37,783 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-07 05:30:37,859 INFO] number of examples: 1803
[2020-12-07 05:30:42,070 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-07 05:30:42,145 INFO] number of examples: 1803
[2020-12-07 05:30:46,693 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-07 05:30:46,874 INFO] number of examples: 1803
[2020-12-07 05:30:50,645 INFO] Step 47850/50000; acc:  99.98; ppl:  1.00; xent: 0.00; lr: 0.00040; 16904/15664 tok/s;  21386 sec
[2020-12-07 05:30:51,031 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-07 05:30:51,105 INFO] number of examples: 1803
[2020-12-07 05:30:55,680 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-07 05:30:55,758 IN

[2020-12-07 05:34:27,826 INFO] number of examples: 1803
[2020-12-07 05:34:32,571 INFO] Step 48300/50000; acc:  99.99; ppl:  1.00; xent: 0.00; lr: 0.00040; 18710/17365 tok/s;  21608 sec
[2020-12-07 05:34:32,576 INFO] Saving checkpoint OpenNMT-py/Data/jamo2char/model/model_step_48300.pt
[2020-12-07 05:34:34,510 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-07 05:34:34,692 INFO] number of examples: 1803
[2020-12-07 05:34:38,898 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-07 05:34:38,972 INFO] number of examples: 1803
[2020-12-07 05:34:43,549 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-07 05:34:43,628 INFO] number of examples: 1803
[2020-12-07 05:34:47,788 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-07 05:34:47,862 INFO] number of examples: 1803
[2020-12-07 05:34:52,395 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-07 05:34:52

[2020-12-07 05:37:51,794 INFO] number of examples: 1803
[2020-12-07 05:37:56,030 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-07 05:37:56,108 INFO] number of examples: 1803
[2020-12-07 05:37:58,386 INFO] Step 48800/50000; acc:  99.98; ppl:  1.00; xent: 0.00; lr: 0.00040; 18834/17552 tok/s;  21814 sec
[2020-12-07 05:37:58,391 INFO] Saving checkpoint OpenNMT-py/Data/jamo2char/model/model_step_48800.pt
[2020-12-07 05:38:02,551 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-07 05:38:02,729 INFO] number of examples: 1803
[2020-12-07 05:38:06,947 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-07 05:38:07,020 INFO] number of examples: 1803
[2020-12-07 05:38:11,592 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-07 05:38:11,670 INFO] number of examples: 1803
[2020-12-07 05:38:15,841 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-07 05:38:15

[2020-12-07 05:41:45,426 INFO] number of examples: 1803
[2020-12-07 05:41:50,010 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-07 05:41:50,089 INFO] number of examples: 1803
[2020-12-07 05:41:54,289 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-07 05:41:54,369 INFO] number of examples: 1803
[2020-12-07 05:41:58,923 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-07 05:41:58,998 INFO] number of examples: 1803
[2020-12-07 05:42:03,189 INFO] Step 49300/50000; acc:  99.98; ppl:  1.00; xent: 0.00; lr: 0.00040; 18764/17408 tok/s;  22059 sec
[2020-12-07 05:42:03,194 INFO] Saving checkpoint OpenNMT-py/Data/jamo2char/model/model_step_49300.pt
[2020-12-07 05:42:05,182 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-07 05:42:05,256 INFO] number of examples: 1803
[2020-12-07 05:42:09,854 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-07 05:42:09

[2020-12-07 05:45:11,521 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-07 05:45:11,706 INFO] number of examples: 1803
[2020-12-07 05:45:16,228 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-07 05:45:16,301 INFO] number of examples: 1803
[2020-12-07 05:45:20,445 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-07 05:45:20,521 INFO] number of examples: 1803
[2020-12-07 05:45:25,068 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-07 05:45:25,144 INFO] number of examples: 1803
[2020-12-07 05:45:27,004 INFO] Step 49800/50000; acc:  99.98; ppl:  1.00; xent: 0.00; lr: 0.00040; 18868/17582 tok/s;  22263 sec
[2020-12-07 05:45:27,009 INFO] Saving checkpoint OpenNMT-py/Data/jamo2char/model/model_step_49800.pt
[2020-12-07 05:45:31,396 INFO] Loading dataset from OpenNMT-py/Data/jamo2char/demo.train.0.pt
[2020-12-07 05:45:31,468 INFO] number of examples: 1803
[2020-12-07 05:45:36

# **Translate**

Now that you have your model, you can start translating.

-model ==> Setting your model

Output predictions into pred.txt

In [24]:
!python OpenNMT-py/translate.py -model OpenNMT-py/Data/jamo2char/model/model_step_50000.pt -src OpenNMT-py/Data/src-test-jamo.txt -output OpenNMT-py/Data/jamo2char/pred_50k.txt -replace_unk -verbose -beam_size 1 -gpu 0

[2020-12-11 15:23:08,830 INFO] Translating shard 0.
[2020-12-11 15:23:09,807 INFO] 
SENT 1: ['"', 'ㄱ', 'ㅕ', 'ㅇ', 'ㅊ', 'ㅏ', 'ㄹ', 'ㅇ', 'ㅢ', 'ᴥ', 'ㅅ', 'ㅓ', 'ㄹ', 'ㅁ', 'ㅕ', 'ㅇ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅂ', 'ㅗ', 'ㅁ', 'ㅕ', 'ㄴ', ',', 'ᴥ', 'ㅅ', 'ㅗ', 'ㄴ', 'ㄴ', 'ㅣ', 'ㅁ', 'ㅇ', 'ㅡ', 'ㄹ', 'ㅗ', 'ᴥ', 'ㅍ', 'ㅣ', 'ㅅ', 'ㅣ', 'ㅂ', 'ㅏ', 'ㅇ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅊ', 'ㅏ', 'ㅈ', 'ㅇ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㄱ', 'ㅣ', 'ㅁ', 'ㅆ', 'ㅣ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㄷ', 'ㅏ', 'ㄹ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅅ', 'ㅗ', 'ㄴ', 'ㄴ', 'ㅣ', 'ㅁ', 'ㅇ', 'ㅣ', 'ᴥ', 'ㄴ', 'ㅏ', 'ㅁ', 'ㄱ', 'ㅣ', 'ㄴ', 'ᴥ', 'ㅇ', 'ㅡ', 'ㅁ', 'ㅅ', 'ㅣ', 'ㄱ', 'ㅁ', 'ㅜ', 'ㄹ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅈ', 'ㅏ', 'ㄹ', 'ㅣ', 'ㅇ', 'ㅔ', 'ㅅ', 'ㅓ', 'ᴥ', 'ㅊ', 'ㅣ', 'ㅇ', 'ㅝ', 'ㄷ', 'ㅏ', 'ㄹ', 'ㄹ', 'ㅏ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅇ', 'ㅛ', 'ㄱ', 'ㅜ', 'ㄹ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅎ', 'ㅏ', 'ㄷ', 'ㅏ', 'ᴥ', 'ㅅ', 'ㅣ', 'ㄴ', 'ㅆ', 'ㅣ', 'ㅇ', 'ㅘ', 'ᴥ', 'ㅁ', 'ㅏ', 'ㄹ', 'ㄷ', 'ㅏ', 'ㅌ', 'ㅜ', 'ㅁ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅎ', 'ㅐ', 'ㅆ', 'ㄷ', 'ㅏ', 'ㄱ', 'ㅗ', 'ᴥ', 'ㅎ', 'ㅏ', 'ㄴ', 'ㄷ', 'ㅏ', '.', '"']
PRED 1: t h e ᴥ k i m ' s ᴥ v e r y ᴥ a n d ᴥ s o t ᴥ t h

[2020-12-11 15:23:10,474 INFO] 
SENT 31: ['"', 'ㄷ', 'ㅏ', 'ㄴ', 'ㄷ', 'ㅗ', 'ㄱ', 'ᴥ', 'ㅋ', 'ㅗ', 'ㄴ', 'ㅅ', 'ㅓ', 'ㅌ', 'ㅡ', 'ᴥ', 'ㅁ', 'ㅜ', 'ㄷ', 'ㅐ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㅇ', 'ㅏ', 'ㄴ', 'ㅣ', 'ㄴ', ',', 'ᴥ', 'ㅈ', 'ㅜ', 'ᴥ', 'ㅅ', 'ㅣ', 'ㅊ', 'ㅓ', 'ㅇ', 'ㅊ', 'ㅡ', 'ㅇ', 'ㅇ', 'ㅣ', 'ᴥ', 'ㅊ', 'ㅓ', 'ㅇ', 'ㅅ', 'ㅗ', 'ㄴ', 'ㅕ', 'ㄴ', 'ㄷ', 'ㅡ', 'ㄹ', 'ㅇ', 'ㅣ', 'ㄴ', 'ᴥ', 'ㅅ', 'ㅣ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㅅ', 'ㅣ', 'ㄱ', 'ᴥ', 'ㅁ', 'ㅜ', 'ㄷ', 'ㅐ', 'ㅇ', 'ㅕ', 'ㅆ', 'ㄷ', 'ㅏ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅈ', 'ㅓ', 'ㅁ', 'ㅇ', 'ㅔ', 'ㅅ', 'ㅓ', 'ᴥ', 'ㅎ', 'ㅘ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㅢ', 'ᴥ', 'ㅇ', 'ㅢ', 'ㅅ', 'ㅏ', 'ㅇ', 'ᴥ', 'ㅅ', 'ㅓ', 'ㄴ', 'ㅌ', 'ㅐ', 'ㄱ', 'ㅇ', 'ㅔ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅇ', 'ㅏ', 'ㅅ', 'ㅟ', 'ㅇ', 'ㅜ', 'ㅁ', 'ㅇ', 'ㅣ', 'ᴥ', 'ㄴ', 'ㅏ', 'ㅁ', 'ㄴ', 'ㅡ', 'ㄴ', 'ㄷ', 'ㅏ', '.', '"']
PRED 31: " s e o u l a t e r , ᴥ t h e ᴥ c h o u r s ᴥ i s ᴥ e v e r y ᴥ o f ᴥ t h e ᴥ s t o r y . "
PRED SCORE: -0.0967

[2020-12-11 15:23:10,474 INFO] 
SENT 32: ['"', 'ㅊ', 'ㅜ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㅊ', 'ㅟ', 'ㅇ', 'ㅓ', 'ㅂ', 'ᴥ', 'ㅎ', 'ㅢ', 'ㅁ', 'ㅏ', 'ㅇ', 'ㅈ', 'ㅏ', 'ㅇ', 'ㅔ', 'ㄷ', 'ㅏ', 'ᴥ', 'ㄱ',

[2020-12-11 15:23:11,144 INFO] 
SENT 61: ['ㅇ', 'ㅣ', 'ㅇ', 'ㅘ', 'ᴥ', 'ㄷ', 'ㅏ', 'ㄹ', 'ㄹ', 'ㅣ', 'ᴥ', 'ㅇ', 'ㅜ', 'ㄱ', 'ㅣ', 'ㅇ', 'ㅔ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅁ', 'ㅗ', 'ㄱ', 'ㅊ', 'ㅗ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㅁ', 'ㅜ', 'ㅅ', 'ㅓ', 'ㅇ', 'ㅎ', 'ㅐ', 'ᴥ', 'ㄱ', 'ㅜ', 'ㅊ', 'ㅜ', 'ㅇ', 'ㅈ', 'ㅔ', 'ㅇ', 'ㅘ', 'ᴥ', 'ㅎ', 'ㅏ', 'ㅇ', 'ㅅ', 'ㅐ', 'ㅇ', 'ㅈ', 'ㅔ', 'ㅇ', 'ㅢ', 'ᴥ', 'ㅅ', 'ㅜ', 'ㅇ', 'ㅛ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㄴ', 'ㅗ', 'ㅍ', 'ㄷ', 'ㅏ', '.']
PRED 61: t h i s ᴥ i s ᴥ a n ᴥ a r e ᴥ n o t ᴥ w i t h ᴥ t h e ᴥ m o v e ᴥ i m p o r t a n t .
PRED SCORE: -0.0978

[2020-12-11 15:23:11,144 INFO] 
SENT 62: ['ㄷ', 'ㅐ', 'ㅈ', 'ㅓ', 'ㄴ', 'ㅈ', 'ㅣ', 'ㅇ', 'ㅕ', 'ㄱ', 'ᴥ', 'ㄱ', 'ㅕ', 'ㅇ', 'ㅈ', 'ㅔ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㅎ', 'ㅡ', 'ㄴ', 'ㄷ', 'ㅡ', 'ㄹ', 'ㄹ', 'ㅣ', 'ㄱ', 'ㅗ', 'ᴥ', 'ㅇ', 'ㅣ', 'ㅆ', 'ㄷ', 'ㅏ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅌ', 'ㅗ', 'ㅇ', 'ㄱ', 'ㅖ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㅈ', 'ㅣ', 'ㄴ', 'ㅏ', 'ㄴ', 'ㅎ', 'ㅐ', 'ㅂ', 'ㅜ', 'ㅌ', 'ㅓ', 'ᴥ', 'ㅇ', 'ㅕ', 'ㄴ', 'ㅇ', 'ㅣ', 'ㅇ', 'ㅓ', 'ᴥ', 'ㄴ', 'ㅏ', 'ㅇ', 'ㅗ', 'ㄱ', 'ㅗ', 'ᴥ', 'ㅇ', 'ㅣ', 'ㅆ', 'ㄷ', 'ㅏ', '.']
PRED 62: i ᴥ t h i n k ᴥ i t ' s ᴥ t i m e ᴥ 

[2020-12-11 15:23:11,819 INFO] 
SENT 91: ['"', 'ㅅ', 'ㅗ', 'ㄴ', 'ㅅ', 'ㅓ', 'ㄱ', 'ㅎ', 'ㅢ', 'ᴥ', 'j', 't', 'b', 'c', 'ᴥ', 'ㄷ', 'ㅐ', 'ㅍ', 'ㅛ', 'ㅇ', 'ㅣ', 'ㅅ', 'ㅏ', 'ㄹ', 'ㅗ', 'ㅂ', 'ㅜ', 'ㅌ', 'ㅓ', 'ᴥ', 'ㅍ', 'ㅗ', 'ㄱ', 'ㅎ', 'ㅐ', 'ㅇ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㄷ', 'ㅏ', 'ㅇ', 'ㅎ', 'ㅐ', 'ㅆ', 'ㄷ', 'ㅏ', 'ㄱ', 'ㅗ', 'ᴥ', 'ㅈ', 'ㅜ', 'ㅈ', 'ㅏ', 'ㅇ', 'ㅎ', 'ㅏ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅍ', 'ㅡ', 'ㄹ', 'ㅣ', 'ㄹ', 'ㅐ', 'ㄴ', 'ㅅ', 'ㅓ', 'ᴥ', 'ㄱ', 'ㅣ', 'ㅈ', 'ㅏ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㅅ', 'ㅗ', 'ㄴ', 'ᴥ', 'ㄷ', 'ㅐ', 'ㅍ', 'ㅛ', 'ㄹ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅎ', 'ㅕ', 'ㅂ', 'ㅂ', 'ㅏ', 'ㄱ', ',', 'ᴥ', 'ㅁ', 'ㅕ', 'ㅇ', 'ㅇ', 'ㅖ', 'ㅎ', 'ㅞ', 'ㅅ', 'ㅗ', 'ㄴ', 'ᴥ', 'ㅎ', 'ㅕ', 'ㅁ', 'ㅇ', 'ㅢ', 'ᴥ', 'ㄷ', 'ㅡ', 'ㅇ', 'ㅇ', 'ㅡ', 'ㄹ', 'ㅗ', 'ᴥ', 'ㄱ', 'ㅓ', 'ㅁ', 'ㅊ', 'ㅏ', 'ㄹ', 'ㅇ', 'ㅔ', 'ᴥ', 'ㅊ', 'ㅜ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㄱ', 'ㅗ', 'ㅅ', 'ㅗ', 'ㅎ', 'ㅐ', 'ㅆ', 'ㄷ', 'ㅏ', '.', '"']
PRED 91: " a ᴥ c h o s e , ᴥ s h i n ᴥ i s ᴥ n o t ᴥ t h e ᴥ t i m e ᴥ t o ᴥ r i v i c e . "
PRED SCORE: -0.0974

[2020-12-11 15:23:11,820 INFO] 
SENT 92: ['ㄱ', 'ㅕ', 'ㅇ', 'ㅊ', 'ㅏ', 'ㄹ', 'ㅇ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅅ', 'ㅣ

[2020-12-11 15:23:12,466 INFO] 
SENT 121: ['ㄱ', 'ㅡ', 'ᴥ', 'ㄱ', 'ㅘ', 'ㅈ', 'ㅓ', 'ㅇ', 'ㅇ', 'ㅔ', 'ㅅ', 'ㅓ', 'ᴥ', 'ㄱ', 'ㅏ', 'ㅈ', 'ㅏ', 'ㅇ', 'ᴥ', 'ㅈ', 'ㅜ', 'ㅇ', 'ㅅ', 'ㅣ', 'ㅎ', 'ㅏ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㄱ', 'ㅓ', 'ㅅ', 'ㅇ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅁ', 'ㅏ', 'ㄴ', 'ㅎ', 'ㅘ', 'ㅇ', 'ㅢ', 'ᴥ', 'ㅌ', 'ㅡ', 'ㄱ', 'ㅂ', 'ㅕ', 'ㄹ', 'ㅎ', 'ㅏ', 'ㄴ', 'ᴥ', 'ㅇ', 'ㅖ', 'ㅅ', 'ㅜ', 'ㄹ', 'ㅅ', 'ㅓ', 'ㅇ', 'ㅇ', 'ㅔ', 'ᴥ', 'ㅁ', 'ㅏ', 'ㄴ', 'ㅎ', 'ㅘ', 'ㄱ', 'ㅏ', 'ㅃ', 'ㅜ', 'ㄴ', 'ᴥ', 'ㅇ', 'ㅏ', 'ㄴ', 'ㅣ', 'ㄹ', 'ㅏ', 'ᴥ', 'ㅁ', 'ㅗ', 'ㄷ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㄱ', 'ㅜ', 'ㄱ', 'ㅁ', 'ㅣ', 'ㄴ', 'ㅇ', 'ㅣ', 'ᴥ', 'ㅎ', 'ㅏ', 'ㅁ', 'ㄲ', 'ㅔ', 'ᴥ', 'ㅊ', 'ㅏ', 'ㅁ', 'ㅇ', 'ㅕ', 'ㅎ', 'ㅏ', 'ㄹ', 'ᴥ', 'ㅅ', 'ㅜ', 'ᴥ', 'ㅇ', 'ㅣ', 'ㅆ', 'ㄷ', 'ㅗ', 'ㄹ', 'ㅗ', 'ㄱ', 'ᴥ', 'ㅎ', 'ㅏ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㄱ', 'ㅓ', 'ㅅ', 'ㅇ', 'ㅣ', 'ㄷ', 'ㅏ', '.']
PRED 121: i t ᴥ i s ᴥ a ᴥ s o ᴥ n o t ᴥ b e ᴥ a b l e ᴥ t o ᴥ c a m e ᴥ t o ᴥ b e ᴥ a n d ᴥ c h a n g e .
PRED SCORE: -0.0975

[2020-12-11 15:23:12,466 INFO] 
SENT 122: ['"', 'ㅂ', 'ㅜ', 'ㅅ', 'ㅏ', 'ㄴ', 'ㄱ', 'ㅘ', 'ᴥ', 'ㄷ', 'ㅐ', 'ㄱ', 'ㅜ', 'ㄷ', 'ㅗ', 'ᴥ', 'ㄱ', 'ㅏ

...

[2020-12-11 15:26:05,576 INFO] 
SENT 7891: ['ㄱ', 'ㅡ', 'ㅈ', 'ㅜ', 'ㅇ', 'ᴥ', 'ㅎ', 'ㅏ', 'ㄴ', 'ㅏ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㄷ', 'ㅗ', 'ㅅ', 'ㅣ', 'ㄱ', 'ㅖ', 'ㅎ', 'ㅚ', 'ㄱ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅌ', 'ㅗ', 'ㅇ', 'ㅎ', 'ㅏ', 'ㄴ', 'ᴥ', 'ㄱ', 'ㅗ', 'ㅇ', 'ㄷ', 'ㅗ', 'ㅇ', 'ㅊ', 'ㅔ', 'ᴥ', 'ㅈ', 'ㅗ', 'ㅅ', 'ㅓ', 'ㅇ', 'ㄱ', 'ㅘ', 'ᴥ', 'ㄱ', 'ㅗ', 'ㅇ', 'ㅇ', 'ㅠ', 'ㄱ', 'ㅏ', 'ㅊ', 'ㅣ', 'ᴥ', 'ㅅ', 'ㅣ', 'ㄹ', 'ㅎ', 'ㅕ', 'ㄴ', 'ㅇ', 'ㅣ', 'ㄷ', 'ㅏ', '.']
PRED 7891: h e ᴥ i s ᴥ u r n e d ᴥ s e v e r ᴥ c h o i s ᴥ o n ᴥ t h e ᴥ u p ᴥ a s e m i n g .
PRED SCORE: -0.0970

[2020-12-11 15:26:05,576 INFO] 
SENT 7892: ['ㅁ', 'ㅗ', 'ㄷ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅁ', 'ㅔ', 'ㅁ', 'ㅂ', 'ㅓ', 'ㄱ', 'ㅏ', 'ᴥ', '1', '0', 'ㄷ', 'ㅐ', 'ㄹ', 'ㅗ', 'ᴥ', 'ㄱ', 'ㅜ', 'ㅅ', 'ㅓ', 'ㅇ', 'ㄷ', 'ㅚ', 'ㄴ', 'ᴥ', '6', 'ㅇ', 'ㅣ', 'ㄴ', 'ㅈ', 'ㅗ', 'ᴥ', 'ㄱ', 'ㅡ', 'ㄹ', 'ㅜ', 'ㅂ', 'ᴥ', 'ㄷ', 'ㅓ', 'ᴥ', 'ㅇ', 'ㅣ', 'ㅅ', 'ㅡ', 'ㅌ', 'ㅡ', 'ᴥ', 'ㄹ', 'ㅏ', 'ㅇ', 'ㅣ', 'ㅌ', 'ㅡ', 'ᴥ', 'ㅍ', 'ㅗ', 'ㄱ', 'ㅎ', 'ㅐ', 'ㅇ', 'ᴥ', 'ㅅ', 'ㅏ', 'ㄱ', 'ㅓ', 'ㄴ', 'ㅇ', 'ㅢ', 'ᴥ', 'ㅊ', 'ㅓ', 'ㄹ', 'ㅈ', 'ㅓ', 'ㅎ', 'ㅏ', 'ㄴ', 'ᴥ', 'ㅅ', 'ㅜ', 'ㅅ', 'ㅏ', '

[2020-12-11 15:26:06,387 INFO] 
SENT 7921: ['ㄱ', 'ㅝ', 'ㄴ', 'ㅇ', 'ㅛ', 'ㅇ', 'ㅅ', 'ㅜ', 'ᴥ', 'ㅈ', 'ㅜ', 'ㅇ', 'ㅜ', 'ㅈ', 'ㅡ', 'ㅂ', 'ㅔ', 'ㅋ', 'ㅣ', 'ㅅ', 'ㅡ', 'ㅌ', 'ㅏ', 'ㄴ', 'ᴥ', 'ㄷ', 'ㅐ', 'ㅅ', 'ㅏ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅅ', 'ㅡ', 'ㅁ', 'ㅏ', 'ㅌ', 'ㅡ', 'ㅁ', 'ㅣ', 'ㅌ', 'ㅓ', 'ᴥ', 'ㅍ', 'ㅡ', 'ㄹ', 'ㅗ', 'ㅈ', 'ㅔ', 'ㄱ', 'ㅌ', 'ㅡ', 'ㅇ', 'ㅢ', 'ᴥ', 'ㅅ', 'ㅓ', 'ㅇ', 'ㄱ', 'ㅗ', 'ㅇ', 'ᴥ', 'ㅊ', 'ㅜ', 'ㅈ', 'ㅣ', 'ㄴ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅂ', 'ㅏ', 'ㅌ', 'ㅏ', 'ㅇ', 'ㅇ', 'ㅡ', 'ㄹ', 'ㅗ', 'ᴥ', 'k', 't', 'ㅇ', 'ㅢ', 'ᴥ', 'ㅇ', 'ㅜ', 'ㅈ', 'ㅡ', 'ㅂ', 'ㅔ', 'ㄱ', 'ᴥ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㅓ', 'ㅂ', 'ㅇ', 'ㅣ', 'ᴥ', 'ㄷ', 'ㅏ', 'ㅇ', 'ㅑ', 'ㅇ', 'ㅎ', 'ㅏ', 'ㄴ', 'ᴥ', 'i', 'c', 't', 'ᴥ', 'ㅂ', 'ㅜ', 'ㄴ', 'ㅇ', 'ㅑ', 'ㄹ', 'ㅗ', 'ᴥ', 'ㅎ', 'ㅘ', 'ㄱ', 'ㄷ', 'ㅐ', 'ㄷ', 'ㅙ', 'ᴥ', 'ㄴ', 'ㅏ', 'ㄱ', 'ㅏ', 'ㄱ', 'ㅣ', 'ㄹ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅂ', 'ㅏ', 'ㄹ', 'ㅏ', 'ㄴ', 'ㄷ', 'ㅏ', 'ㄱ', 'ㅗ', 'ᴥ', 'ㅂ', 'ㅏ', 'ㄺ', 'ㅎ', 'ㅕ', 'ㅆ', 'ㄷ', 'ㅏ', '.']
PRED 7921: s h i n k i n g ᴥ s h o u l d ᴥ b e ᴥ a ᴥ s i n c e ᴥ t h e ᴥ c h o i s t o r y ᴥ p l a y e r .
PRED SCORE: -0.0975

[2020-12-11 15:26:06,38

[2020-12-11 15:26:07,205 INFO] 
SENT 7951: ['ㅋ', 'ㅏ', 'ㅌ', 'ㅏ', 'ㄹ', 'ㅡ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', '4', 'ㄱ', 'ㅕ', 'ㅇ', 'ㄱ', 'ㅣ', 'ㅅ', 'ㅓ', 'ᴥ', '1', '0', 'ㄱ', 'ㅗ', 'ㄹ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅎ', 'ㅓ', 'ㅇ', 'ㅛ', 'ㅇ', 'ㅎ', 'ㅐ', 'ㅆ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅈ', 'ㅓ', 'ㅇ', 'ㄷ', 'ㅗ', 'ㄹ', 'ㅗ', 'ᴥ', 'ㅅ', 'ㅜ', 'ㅂ', 'ㅣ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㅇ', 'ㅑ', 'ㄱ', 'ㅎ', 'ㅏ', 'ㄴ', 'ᴥ', 'ㅌ', 'ㅣ', 'ㅁ', 'ㅇ', 'ㅣ', 'ㄱ', 'ㅣ', 'ᴥ', 'ㄸ', 'ㅐ', 'ㅁ', 'ㅜ', 'ㄴ', 'ㅇ', 'ㅔ', 'ᴥ', 'ㅈ', 'ㅓ', 'ㅇ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㅈ', 'ㅓ', 'ㄱ', 'ㅇ', 'ㅡ', 'ㄹ', 'ㅗ', 'ᴥ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㄷ', 'ㅐ', 'ㅎ', 'ㅏ', 'ㅁ', 'ㅕ', 'ㄴ', 'ᴥ', 'ㅊ', 'ㅜ', 'ㅇ', 'ㅂ', 'ㅜ', 'ㄴ', 'ㅎ', 'ㅣ', 'ᴥ', 'ㅇ', 'ㅣ', 'ㄱ', 'ㅣ', 'ㄹ', 'ᴥ', 'ㅅ', 'ㅜ', 'ᴥ', 'ㅇ', 'ㅣ', 'ㅆ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㄷ', 'ㅐ', 'ㄷ', 'ㅏ', '.']
PRED 7951: s o ᴥ t h e ᴥ b e n t ᴥ f o r ᴥ m o v e ᴥ i n ᴥ t h e ᴥ c a r e ᴥ b e i n g ᴥ a m e ᴥ d a y .
PRED SCORE: -0.0972

[2020-12-11 15:26:07,206 INFO] 
SENT 7952: ['ㄷ', 'ㅐ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㅇ', 'ㅔ', 'ㅅ', 'ㅓ', 'ᴥ', 'ㅈ', 'ㅔ', 'ㅈ', 'ㅗ', 'ㅎ', 'ㅏ', 'ㄴ', 'ᴥ', 'ㅊ', 'ㅓ', 'ㅇ', '

[2020-12-11 15:26:08,016 INFO] 
SENT 7981: ['"', 'ㄱ', 'ㅡ', 'ㄴ', 'ㄷ', 'ㅐ', 'ㄱ', 'ㅓ', 'ㄴ', 'ㅊ', 'ㅜ', 'ㄱ', 'ㅁ', 'ㅜ', 'ㄹ', 'ᴥ', 'ㄱ', 'ㅣ', 'ㄹ', 'ㅗ', 'ㄱ', 'ㅂ', 'ㅗ', 'ㅈ', 'ㅗ', 'ㄴ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㅓ', 'ㅂ', 'ㅇ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅈ', 'ㅣ', 'ㄴ', 'ㅏ', 'ㄴ', 'ᴥ', '2', '0', '1', '0', 'ㄴ', 'ㅕ', 'ㄴ', 'ㅂ', 'ㅜ', 'ㅌ', 'ㅓ', 'ᴥ', 'ㄱ', 'ㅘ', 'ㅇ', 'ㅈ', 'ㅜ', 'ㅅ', 'ㅣ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㅊ', 'ㅜ', 'ㅈ', 'ㅣ', 'ㄴ', 'ㅎ', 'ㅏ', 'ㄱ', 'ㅗ', 'ᴥ', 'ㅇ', 'ㅣ', 'ㅆ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㅓ', 'ㅂ', 'ㅇ', 'ㅡ', 'ㄹ', 'ㅗ', ',', 'ᴥ', 'ㄱ', 'ㅡ', 'ㄷ', 'ㅗ', 'ㅇ', 'ㅇ', 'ㅏ', 'ㄴ', 'ᴥ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㅓ', 'ㅂ', 'ㄷ', 'ㅐ', 'ㅅ', 'ㅏ', 'ㅇ', 'ᴥ', 'ㄱ', 'ㅓ', 'ㄴ', 'ㅁ', 'ㅜ', 'ㄹ', 'ㅈ', 'ㅜ', 'ㅇ', 'ㅢ', 'ᴥ', 'ㅂ', 'ㅣ', 'ㅎ', 'ㅕ', 'ㅂ', 'ㅈ', 'ㅗ', 'ㅇ', 'ㅘ', 'ᴥ', 'ㄱ', 'ㅓ', 'ㄴ', 'ㅊ', 'ㅜ', 'ㄱ', 'ㅁ', 'ㅜ', 'ㄹ', 'ᴥ', 'ㅅ', 'ㅏ', 'ㄴ', 'ㅈ', 'ㅐ', 'ㄹ', 'ㅗ', 'ᴥ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㅓ', 'ㅂ', 'ㅊ', 'ㅜ', 'ㅈ', 'ㅣ', 'ㄴ', 'ㅇ', 'ㅔ', 'ᴥ', 'ㅈ', 'ㅓ', 'ㄱ', 'ㅈ', 'ㅣ', 'ᴥ', 'ㅇ', 'ㅏ', 'ㄶ', 'ㅇ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅇ', 'ㅓ', 'ㄹ', 'ㅕ', 'ㅇ', 'ㅜ', 'ㅁ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㄱ', 'ㅕ', 'ㄲ', 'ㅇ', '

[2020-12-11 15:26:08,621 INFO] 
SENT 8011: ['ㄷ', 'ㅏ', 'ㅁ', 'ㅏ', 'ㄴ', 'ᴥ', 'ㅂ', 'ㅜ', 'ㄱ', 'ㅁ', 'ㅣ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㄱ', 'ㅗ', 'ㅇ', 'ㄷ', 'ㅗ', 'ㅇ', 'ᴥ', 'ㅇ', 'ㅠ', 'ㅎ', 'ㅐ', 'ㅂ', 'ㅏ', 'ㄹ', 'ㄱ', 'ㅜ', 'ㄹ', 'ᴥ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㅓ', 'ㅂ', 'ㅇ', 'ㅔ', 'ᴥ', 'ㅎ', 'ㅏ', 'ㅂ', 'ㅇ', 'ㅢ', 'ㅎ', 'ㅏ', 'ㄴ', 'ㄷ', 'ㅏ', 'ㅁ', 'ㅕ', 'ㄴ', 'ᴥ', 'ㅁ', 'ㅣ', 'ㄱ', 'ㅜ', 'ㄱ', 'ᴥ', 'ㅈ', 'ㅏ', 'ㅇ', 'ㅂ', 'ㅣ', 'ㅇ', 'ㅢ', 'ᴥ', 'ㄷ', 'ㅐ', 'ㅂ', 'ㅜ', 'ㄱ', 'ᴥ', 'ㅂ', 'ㅏ', 'ㄴ', 'ㅇ', 'ㅣ', 'ㅂ', 'ㄱ', 'ㅘ', 'ᴥ', 'ㅂ', 'ㅏ', 'ㄹ', 'ㄱ', 'ㅜ', 'ㄹ', 'ᴥ', 'ㅂ', 'ㅣ', 'ㅇ', 'ㅛ', 'ㅇ', 'ᴥ', 'ㅈ', 'ㅣ', 'ㅂ', 'ㅜ', 'ㄹ', 'ᴥ', 'ㄷ', 'ㅡ', 'ㅇ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅇ', 'ㅟ', 'ㅎ', 'ㅏ', 'ㄴ', 'ᴥ', 'ㄷ', 'ㅐ', 'ㅂ', 'ㅜ', 'ㄱ', 'ㅈ', 'ㅔ', 'ㅈ', 'ㅐ', 'ᴥ', 'ㅇ', 'ㅖ', 'ㅇ', 'ㅚ', 'ᴥ', 'ㅇ', 'ㅣ', 'ㄴ', 'ㅈ', 'ㅓ', 'ㅇ', 'ㅇ', 'ㅣ', 'ᴥ', 'ㅍ', 'ㅣ', 'ㄹ', 'ㅇ', 'ㅛ', 'ㅎ', 'ㅏ', 'ㄷ', 'ㅏ', '.']
PRED 8011: m e d i c a l ᴥ p r e s e n t ᴥ c a m e ᴥ a t ᴥ t h e ᴥ r e m a i n g ᴥ i n ᴥ s h o t .
PRED SCORE: -0.0965

[2020-12-11 15:26:08,621 INFO] 
SENT 8012: ['ㅊ', 'ㅜ', 'ㄹ', 'ㅅ', 'ㅏ', 'ㄴ', 'ㄱ', 'ㅘ', 'ᴥ', 'ㅇ

# Detokenization

Even after the translation process is finished, it is still in a segment, so it is different from the actual sentence structure used by real people. Thus, when you perform a detoxification process, it is returned in the form of the actual sentence.

We Use "sed" for BPE Detokenization


In [7]:
!sed -i "s/@@ //g"  OpenNMT-py/Data/pred.txt

# Post-processing

In [10]:
f = open('OpenNMT-py/Data/tgt-test-char.txt', 'r', encoding='utf-8')
txt = f.read()
txt = txt.replace(' ', '')
txt = txt.replace('ᴥ', ' ')

with open("OpenNMT-py/Data/tgt-test-char-edited.txt", "w") as f:
    f.write(txt)
    
txt[:1000]    

'"according to descriptions by the police, mr. kim, who visited the pc-bang as a guest, had an argument with mr. shin while demanding that food left by other guests be cleared from his seat."\n"as jamsil girls\' high school (principal kim in-bong) is aiming to cultivate talents and good personality, the teachers and students are upgrading their career path programs through the ""team-play of trust""."\nformer lawmaker kim will lose both his right to vote and his right to run for 5 years if a fine of 1 million won or more is confirmed.\n"the working environment of daejeon industrial park in daedeok-gu, daejeon will be improved."\n"around 90t of reinforcement facilities were lost due to high waves at the dongbang breakwater construction site in wimi port, namwon-eup, seogwipo-si, and a 100m median strip fell in the area of nohyeong rotary - samsung service center in jeju."\nit is a program to make students value physical education and art.\n"the us department of justice prosecuted assang

In [25]:
f = open('OpenNMT-py/Data/jamo2char/pred_50k.txt', 'r', encoding='utf-8')
txt = f.read()
txt = txt.replace(' ', '')
txt = txt.replace('ᴥ', ' ')

with open("OpenNMT-py/Data/jamo2char/pred_50k-edited.txt", "w", encoding='utf-8') as f:
    f.write(txt)

f = open('OpenNMT-py/Data/jamo2char/pred_50k-edited.txt', 'r', encoding='utf-8')
txt = f.read()
txt[:1000]  

'the kim\'s very and sot the first of minderest.\nchoi have to go can a seem.\n"that\'s about kim sellis has ain first age."\nit\'s so have to change that he first year.\nit was for a should such a keep well to the reas.\nthe because is to preasons for the costing.\n"came of the but review, it\'s proparted 10 people."\n"the two more at 17 the can lost work in loved."\nthe useas the is monthing at coulding to stopices.\n"a the care, the two should pizal in the distor."\n"he change, shis can be a lot a lot of world at."\ni also something and that face the possing juse.\n"he fact, is treestion insials are of my being."\n"secuse to help came be drealts not to last."\n"in a fact, a little several are of the bunde."\n"about the 50,000 of should good me first but."\nthe chance seeions are the face in know.\n"now, his being is always to could not far a lot."\nsech kim\'s seed a for the of oviceors is not it.\nchoi has a presed as the first a seviculed again.\n"when first or every what the firs

# Evaluation Using BLEU

Quantitative evaluation is performed on the sentence thus obtained. BLEU is a quantitative evaluation method for machine translation. You can see which model is superior by comparing it to the BLEU score you are comparing.

https://www.aclweb.org/anthology/P02-1040

In [26]:
!perl  OpenNMT-py/tools/multi-bleu.perl OpenNMT-py/Data/tgt-test-char-edited.txt < OpenNMT-py/Data/jamo2char/pred_50k-edited.txt

BLEU = 0.03, 19.9/0.8/0.0/0.0 (BP=0.140, ratio=0.337, hyp_len=76659, ref_len=227303)
